In [1]:
from pyevolve import G1DList
from pyevolve import GSimpleGA
from pyevolve import Selectors
from pyevolve import Statistics
from pyevolve import Mutators
from random import shuffle, randint
from pyevolve import Util
import math

In [2]:
# Define the GPS coordinates of each city
LAT = [16.47, 16.47, 20.09, 22.39, 25.23, 22.00, 20.47, 
          17.20, 16.30, 14.05, 16.53, 21.52, 19.41, 20.09]

LON = [96.10, 94.44, 92.54, 93.37, 97.24, 96.05, 97.02, 
          96.29, 97.38, 98.12, 97.38, 95.59, 97.13, 94.55]

EARTH_RADIUS = 6373.0# approximate radius of earth in km

In [3]:
# Compute the distance between 2 cities using the Haversine formula
def distance(from_city, to_city):
    # Convert to degrees
    from_longitude = math.radians(LON[from_city])
    from_latitude = math.radians(LAT[from_city])
    to_longitude = math.radians(LON[to_city])
    to_latitude = math.radians(LAT[to_city])
    
    # Calculate the coordonate differences
    deltaLon = to_longitude - from_longitude
    deltaLat = to_latitude - from_latitude
    
    # Calculate ande return the distance n km
    a = math.sin(deltaLat / 2)**2 + math.cos(from_latitude) * math.cos(to_latitude) * math.sin(deltaLon / 2)**2
    return  2 * math.atan2(math.sqrt(a), math.sqrt(1 - a)) * EARTH_RADIUS

In [52]:
def customInitializator(genome, **args):
    """Unique integer initializator, generate a range from 0 to genomeSize and shuffle it
    """
    genomeList = list(range(0, genome.getListSize()))
    shuffle(genomeList)
    genome.genomeList = genomeList

def customCrossOver(genome, **args):
    """ Keep one 

    """
    
    sister = None
    brother = None
    gMom = args["mom"]
    gDad = args["dad"]
    #print("mom", gMom)
    #print("dad", gDad)

    if len(gMom) == 1:
        Util.raiseException("The 1D List have one element, can't use the Single Point Crossover method !", TypeError)

    cut = randint(1, len(gMom) - 1)
    #print("cut: ", cut)

    if args["count"] >= 1:
        # cross with mum and dad
        sister = gMom.clone()
        sister.resetStats()
        sister[cut:] = gDad[cut:]
        
        # make sure that cities are present only one time
        sample = list(range(gMom.getListSize()))
        for i in range(len(sister)):
            if(sister[i] in sample):
                sample.remove(sister[i])
            else:
                index = randint(0, len(sample) - 1)
                sister[i] = sample[index]
                sample.pop(index)

    if args["count"] == 2:
        brother = gDad.clone()
        brother.resetStats()
        brother[cut:] = gMom[cut:]
        
        # make sure that cities are present only one time
        sample = list(range(gMom.getListSize()))
        for i in range(len(brother)):
            if(brother[i] in sample):
                sample.remove(brother[i])
            else:
                index = randint(0, len(sample) - 1)
                brother[i] = sample[index]
                sample.pop(index)

    return (sister, brother)

In [9]:
def fitness(chromosome):
    score = 0.0
    # iterate over the chromosome
    for i in range(1,len(chromosome)):
        score += distance(chromosome[i - 1], chromosome[i])
    return 1/float(score) * 10000

In [6]:
def current_best(ga_engine):
    # Here you have access to the GA Engine
    print(ga.bestIndividual())
    return False

In [53]:
# Chromosome representation

# genome = list of destinations possible
genome = G1DList.G1DList(14)

# how to initialize the genome
genome.initializator.set(customInitializator)
#genome.setParams(rangemin=0, rangemax=10, gauss_mu=0, gauss_sigma=1)

# how to mutate a chromosome
#(keep the default one, swap 2 random elements)
#genome.mutator.set(Mutators.G1DListMutatorSwap)

#how to crossover a chromosome
genome.crossover.set(customCrossOver)

# how to compute the fitness
genome.evaluator.set(fitness)

# GA initialisation
ga = GSimpleGA.GSimpleGA(genome, seed=999)
ga.setPopulationSize(100)
ga.setMutationRate(0.01)
ga.setCrossoverRate(0.9)
ga.selector.set(Selectors.GTournamentSelector)
ga.setElitism(True)

# Number of generations
ga.setGenerations(100)

# In case we want to monitor the evolution process
# execute the function current_best every generation
#ga.stepCallback.set(current_best)

ga.evolve(freq_stats=10)

# Final best solution
print(ga.bestIndividual())

Gen. 0 (0.00%): Max/Min/Avg Fitness(Raw) [1.92(2.42)/1.47(1.26)/1.60(1.60)]
mom - GenomeBase
	Score:			 1.498652
	Fitness:		 1.560547

	Params:		 {}

	Slot [Evaluator] (Count: 1)
		Name: fitness - Weight: 0.50
	Slot [Initializator] (Count: 1)
		Name: customInitializator - Weight: 0.50
		Doc: Unique integer initializator, generate a range from 0 to genomeSize and shuffle it
    
	Slot [Mutator] (Count: 1)
		Name: G1DListMutatorSwap - Weight: 0.50
		Doc:  The mutator of G1DList, Swap Mutator

   .. note:: this mutator is :term:`Data Type Independent`

   
	Slot [Crossover] (Count: 1)
		Name: customCrossOver - Weight: 0.50
		Doc:  Keep one 

    

- G1DList
	List size:	 14
	List:		 [6, 12, 1, 3, 11, 4, 0, 2, 10, 13, 7, 8, 5, 9]


dad - GenomeBase
	Score:			 1.508794
	Fitness:		 1.564517

	Params:		 {}

	Slot [Evaluator] (Count: 1)
		Name: fitness - Weight: 0.50
	Slot [Initializator] (Count: 1)
		Name: customInitializator - Weight: 0.50
		Doc: Unique integer initializator, generate a range

mom - GenomeBase
	Score:			 1.959690
	Fitness:		 1.989095

	Params:		 {}

	Slot [Evaluator] (Count: 1)
		Name: fitness - Weight: 0.50
	Slot [Initializator] (Count: 1)
		Name: customInitializator - Weight: 0.50
		Doc: Unique integer initializator, generate a range from 0 to genomeSize and shuffle it
    
	Slot [Mutator] (Count: 1)
		Name: G1DListMutatorSwap - Weight: 0.50
		Doc:  The mutator of G1DList, Swap Mutator

   .. note:: this mutator is :term:`Data Type Independent`

   
	Slot [Crossover] (Count: 1)
		Name: customCrossOver - Weight: 0.50
		Doc:  Keep one 

    

- G1DList
	List size:	 14
	List:		 [8, 9, 10, 0, 7, 11, 13, 2, 4, 12, 5, 1, 3, 6]


dad - GenomeBase
	Score:			 2.086943
	Fitness:		 2.082171

	Params:		 {}

	Slot [Evaluator] (Count: 1)
		Name: fitness - Weight: 0.50
	Slot [Initializator] (Count: 1)
		Name: customInitializator - Weight: 0.50
		Doc: Unique integer initializator, generate a range from 0 to genomeSize and shuffle it
    
	Slot [Mutator] (Count: 1)
		Name:

mom - GenomeBase
	Score:			 3.010898
	Fitness:		 2.719687

	Params:		 {}

	Slot [Evaluator] (Count: 1)
		Name: fitness - Weight: 0.50
	Slot [Initializator] (Count: 1)
		Name: customInitializator - Weight: 0.50
		Doc: Unique integer initializator, generate a range from 0 to genomeSize and shuffle it
    
	Slot [Mutator] (Count: 1)
		Name: G1DListMutatorSwap - Weight: 0.50
		Doc:  The mutator of G1DList, Swap Mutator

   .. note:: this mutator is :term:`Data Type Independent`

   
	Slot [Crossover] (Count: 1)
		Name: customCrossOver - Weight: 0.50
		Doc:  Keep one 

    

- G1DList
	List size:	 14
	List:		 [8, 9, 10, 0, 7, 1, 12, 13, 2, 3, 4, 5, 11, 6]


dad - GenomeBase
	Score:			 2.944167
	Fitness:		 2.679058

	Params:		 {}

	Slot [Evaluator] (Count: 1)
		Name: fitness - Weight: 0.50
	Slot [Initializator] (Count: 1)
		Name: customInitializator - Weight: 0.50
		Doc: Unique integer initializator, generate a range from 0 to genomeSize and shuffle it
    
	Slot [Mutator] (Count: 1)
		Name:

Gen. 10 (10.00%): Max/Min/Avg Fitness(Raw) [2.85(3.08)/1.81(1.54)/2.38(2.38)]
mom - GenomeBase
	Score:			 2.297412
	Fitness:		 2.322741

	Params:		 {}

	Slot [Evaluator] (Count: 1)
		Name: fitness - Weight: 0.50
	Slot [Initializator] (Count: 1)
		Name: customInitializator - Weight: 0.50
		Doc: Unique integer initializator, generate a range from 0 to genomeSize and shuffle it
    
	Slot [Mutator] (Count: 1)
		Name: G1DListMutatorSwap - Weight: 0.50
		Doc:  The mutator of G1DList, Swap Mutator

   .. note:: this mutator is :term:`Data Type Independent`

   
	Slot [Crossover] (Count: 1)
		Name: customCrossOver - Weight: 0.50
		Doc:  Keep one 

    

- G1DList
	List size:	 14
	List:		 [8, 9, 10, 0, 7, 1, 5, 3, 2, 11, 12, 4, 13, 6]


dad - GenomeBase
	Score:			 2.586373
	Fitness:		 2.519349

	Params:		 {}

	Slot [Evaluator] (Count: 1)
		Name: fitness - Weight: 0.50
	Slot [Initializator] (Count: 1)
		Name: customInitializator - Weight: 0.50
		Doc: Unique integer initializator, generate a ran


mom - GenomeBase
	Score:			 3.075272
	Fitness:		 2.972904

	Params:		 {}

	Slot [Evaluator] (Count: 1)
		Name: fitness - Weight: 0.50
	Slot [Initializator] (Count: 1)
		Name: customInitializator - Weight: 0.50
		Doc: Unique integer initializator, generate a range from 0 to genomeSize and shuffle it
    
	Slot [Mutator] (Count: 1)
		Name: G1DListMutatorSwap - Weight: 0.50
		Doc:  The mutator of G1DList, Swap Mutator

   .. note:: this mutator is :term:`Data Type Independent`

   
	Slot [Crossover] (Count: 1)
		Name: customCrossOver - Weight: 0.50
		Doc:  Keep one 

    

- G1DList
	List size:	 14
	List:		 [10, 9, 8, 0, 7, 1, 12, 13, 2, 3, 6, 11, 5, 4]


dad - GenomeBase
	Score:			 2.757713
	Fitness:		 2.721298

	Params:		 {}

	Slot [Evaluator] (Count: 1)
		Name: fitness - Weight: 0.50
	Slot [Initializator] (Count: 1)
		Name: customInitializator - Weight: 0.50
		Doc: Unique integer initializator, generate a range from 0 to genomeSize and shuffle it
    
	Slot [Mutator] (Count: 1)
		Name

...

Gen. 40 (40.00%): Max/Min/Avg Fitness(Raw) [4.48(3.80)/0.00(1.78)/4.21(3.73)]
mom - GenomeBase
	Score:			 3.795031
	Fitness:		 4.475705

	Params:		 {}

	Slot [Evaluator] (Count: 1)
		Name: fitness - Weight: 0.50
	Slot [Initializator] (Count: 1)
		Name: customInitializator - Weight: 0.50
		Doc: Unique integer initializator, generate a range from 0 to genomeSize and shuffle it
    
	Slot [Mutator] (Count: 1)
		Name: G1DListMutatorSwap - Weight: 0.50
		Doc:  The mutator of G1DList, Swap Mutator

   .. note:: this mutator is :term:`Data Type Independent`

   
	Slot [Crossover] (Count: 1)
		Name: customCrossOver - Weight: 0.50
		Doc:  Keep one 

    

- G1DList
	List size:	 14
	List:		 [9, 8, 10, 0, 1, 7, 12, 6, 13, 2, 3, 11, 5, 4]


dad - GenomeBase
	Score:			 3.795031
	Fitness:		 4.475705

	Params:		 {}

	Slot [Evaluator] (Count: 1)
		Name: fitness - Weight: 0.50
	Slot [Initializator] (Count: 1)
		Name: customInitializator - Weight: 0.50
		Doc: Unique integer initializator, generate a ran


mom - GenomeBase
	Score:			 3.795031
	Fitness:		 4.399248

	Params:		 {}

	Slot [Evaluator] (Count: 1)
		Name: fitness - Weight: 0.50
	Slot [Initializator] (Count: 1)
		Name: customInitializator - Weight: 0.50
		Doc: Unique integer initializator, generate a range from 0 to genomeSize and shuffle it
    
	Slot [Mutator] (Count: 1)
		Name: G1DListMutatorSwap - Weight: 0.50
		Doc:  The mutator of G1DList, Swap Mutator

   .. note:: this mutator is :term:`Data Type Independent`

   
	Slot [Crossover] (Count: 1)
		Name: customCrossOver - Weight: 0.50
		Doc:  Keep one 

    

- G1DList
	List size:	 14
	List:		 [9, 8, 10, 0, 1, 7, 12, 6, 13, 2, 3, 11, 5, 4]


dad - GenomeBase
	Score:			 3.795031
	Fitness:		 4.399248

	Params:		 {}

	Slot [Evaluator] (Count: 1)
		Name: fitness - Weight: 0.50
	Slot [Initializator] (Count: 1)
		Name: customInitializator - Weight: 0.50
		Doc: Unique integer initializator, generate a range from 0 to genomeSize and shuffle it
    
	Slot [Mutator] (Count: 1)
		Name

mom - GenomeBase
	Score:			 3.795031
	Fitness:		 4.485880

	Params:		 {}

	Slot [Evaluator] (Count: 1)
		Name: fitness - Weight: 0.50
	Slot [Initializator] (Count: 1)
		Name: customInitializator - Weight: 0.50
		Doc: Unique integer initializator, generate a range from 0 to genomeSize and shuffle it
    
	Slot [Mutator] (Count: 1)
		Name: G1DListMutatorSwap - Weight: 0.50
		Doc:  The mutator of G1DList, Swap Mutator

   .. note:: this mutator is :term:`Data Type Independent`

   
	Slot [Crossover] (Count: 1)
		Name: customCrossOver - Weight: 0.50
		Doc:  Keep one 

    

- G1DList
	List size:	 14
	List:		 [9, 8, 10, 0, 1, 7, 12, 6, 13, 2, 3, 11, 5, 4]


dad - GenomeBase
	Score:			 3.795031
	Fitness:		 4.485880

	Params:		 {}

	Slot [Evaluator] (Count: 1)
		Name: fitness - Weight: 0.50
	Slot [Initializator] (Count: 1)
		Name: customInitializator - Weight: 0.50
		Doc: Unique integer initializator, generate a range from 0 to genomeSize and shuffle it
    
	Slot [Mutator] (Count: 1)
		Name:


mom - GenomeBase
	Score:			 3.795031
	Fitness:		 4.333311

	Params:		 {}

	Slot [Evaluator] (Count: 1)
		Name: fitness - Weight: 0.50
	Slot [Initializator] (Count: 1)
		Name: customInitializator - Weight: 0.50
		Doc: Unique integer initializator, generate a range from 0 to genomeSize and shuffle it
    
	Slot [Mutator] (Count: 1)
		Name: G1DListMutatorSwap - Weight: 0.50
		Doc:  The mutator of G1DList, Swap Mutator

   .. note:: this mutator is :term:`Data Type Independent`

   
	Slot [Crossover] (Count: 1)
		Name: customCrossOver - Weight: 0.50
		Doc:  Keep one 

    

- G1DList
	List size:	 14
	List:		 [9, 8, 10, 0, 1, 7, 12, 6, 13, 2, 3, 11, 5, 4]


dad - GenomeBase
	Score:			 3.795031
	Fitness:		 4.333311

	Params:		 {}

	Slot [Evaluator] (Count: 1)
		Name: fitness - Weight: 0.50
	Slot [Initializator] (Count: 1)
		Name: customInitializator - Weight: 0.50
		Doc: Unique integer initializator, generate a range from 0 to genomeSize and shuffle it
    
	Slot [Mutator] (Count: 1)
		Name

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [46]:
distance(9, 8) + distance(8, 10) + distance(10, 0) + distance(0, 1) + distance(1, 7) + distance(7, 12) + distance(12, 6) + distance(6, 13) + distance(13, 2) + distance(2, 3) + distance(3, 11) + distance(11, 5) + distance(5, 4) 


2635.024862476629

In [50]:
# Generate a graph showing the evolutionary results: fitness vs generations
%run src/pyevolve/pyevolve_graph.py -i log_bit-string -2

Pyevolve 0.6 - Graph Plot Tool
By Christian S. Perone

Loading modules....
Database file 'pyevolve.db' not found !


In [51]:
# Generate a heatmap of population fitness score distribution over generations
%run src/pyevolve/pyevolve_graph.py -i log_bit-string -9

Pyevolve 0.6 - Graph Plot Tool
By Christian S. Perone

Loading modules....
Database file 'pyevolve.db' not found !
